In [2]:
! curl -s https://dl.openfoam.com/add-debian-repo.sh | sudo bash
! sudo apt-get install ca-certificates
! sudo apt-get update
! sudo apt-get install openfoam2206-default

Detected distribution code-name: focal
Added /etc/apt/sources.list.d/openfoam.list
Importing openfoam gpg key... done
Added /etc/apt/trusted.gpg.d/openfoam.gpg
Running apt-get update... done

The repository is setup! You can now install packages.
Reading package lists... Done
Building dependency tree       
Reading state information... Done
ca-certificates is already the newest version (20211016ubuntu0.20.04.1).
0 upgraded, 0 newly installed, 0 to remove and 30 not upgraded.
Hit:1 http://ppa.launchpad.net/c2d4u.team/c2d4u4.0+/ubuntu focal InRelease
Hit:2 https://cloud.r-project.org/bin/linux/ubuntu focal-cran40/ InRelease
Hit:3 http://ppa.launchpad.net/cran/libgit2/ubuntu focal InRelease
Hit:4 http://ppa.launchpad.net/deadsnakes/ppa/ubuntu focal InRelease
Hit:5 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2004/x86_64  InRelease
Hit:6 http://ppa.launchpad.net/graphics-drivers/ppa/ubuntu focal InRelease
Hit:7 http://ppa.launchpad.net/ubuntugis/ppa/ubuntu focal InRelease

In [1]:
! rm -rf templates
! mkdir templates
# upload templates

In [ ]:
from google.colab import drive
# drive.flush_and_unmount()
drive.mount('/content/drive')
%cd /content/drive/MyDrive/GitHub/no-cfd/baseline

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
/content/drive/MyDrive/GitHub/no-cfd/baseline


In [3]:
! git clone https://github.com/MiroslavKabat/pythonNacaProfileGeneratorSTL/

Cloning into 'pythonNacaProfileGeneratorSTL'...
remote: Enumerating objects: 110, done.
remote: Total 110 (delta 0), reused 0 (delta 0), pack-reused 110
Receiving objects: 100% (110/110), 334.29 KiB | 953.00 KiB/s, done.
Resolving deltas: 100% (55/55), done.


In [4]:
import os
import jinja2
import torch
import time


def simulation(case_path, params):

  then = time.perf_counter()
  orig_then = then

  foil_number = params['airfoil_number']
  n_points = params['airfoil_n_points']
  width = params['airfoil_width']
  length = params['airfoil_length']
  attack_angle = params['airfoil_attack_angle']
  min_x = params['domain_min_x']
  max_x = params['domain_max_x']
  min_y = params['domain_min_y']
  max_y = params['domain_max_y']
  min_z = params['domain_min_z']
  max_z = params['domain_max_z']
  n_x = params['sample_n_x']
  n_y = params['sample_n_y']
  n_z = params['sample_n_z']
  n_t = params['sample_n_t']
  blocks_x = params['mesh_resolution_x']
  blocks_y = params['mesh_resolution_y']
  blocks_z = params['mesh_resolution_z']
  level_edges = params['mesh_level_edges']
  level_surface_min = params['mesh_level_surface_min']
  level_surface_max = params['mesh_level_surface_max']
  delta_t = params['sim_delta_t']
  write_interval = params['sim_write_interval']
  velocity = params['domain_inlet_velocity']
  n_procs = params['sim_n_procs']
  max_unbalance = params['sim_max_unbalance']

  os.system(f'rm -rf {case_path}')
  os.system(f'mkdir {case_path}')
  os.system(f'mkdir {case_path}/constant')
  os.system(f'mkdir {case_path}/system')
  os.system(f'mkdir {case_path}/0')
  os.system(f'mkdir {case_path}/constant/triSurface')
  
  os.system('python3 pythonNacaProfileGeneratorSTL/myNaca.py ' +
            f'{foil_number} {n_points} {width} {length} {attack_angle}')
  os.system(f'mv naca{foil_number}.stl {case_path}/constant/triSurface')

  stl_filename = f'naca{foil_number}.stl'
  emesh_filename = f'naca{foil_number}.eMesh'

  end_time = (n_t-1) * delta_t * write_interval

  dim_x = max_x - min_x
  dim_y = max_y - min_y
  dim_z = max_z - min_z
  d_x = dim_x / (n_x-1)
  d_y = dim_y / (n_y-1)
  d_z = dim_z / (n_z-1)

  sample_points = ' '.join(f'({min_x+k_x*d_x} {min_y+k_y*d_y} {min_z+k_z*d_z})'
                           for k_x in range(n_x) for k_y in range(n_y) for k_z in range(n_z))

  render_list = [
      ('controlDict', f'{case_path}/system/controlDict', {'end_time':end_time, 'delta_t':delta_t, 'write_interval':write_interval}),
      ('U', f'{case_path}/0/U', {'velocity':velocity}),
      ('p', f'{case_path}/0/p', {}),
      ('transportProperties', f'{case_path}/constant/transportProperties', {'nu':1.48e-5}),
      ('turbulenceProperties', f'{case_path}/constant/turbulenceProperties', {}),
      ('fvSchemes', f'{case_path}/system/fvSchemes', {}),
      ('fvSolution', f'{case_path}/system/fvSolution', {}),
      ('blockMeshDict', f'{case_path}/system/blockMeshDict', {'min_x':min_x, 'min_y':min_y, 'min_z':min_z, 'max_x':max_x, 'max_y':max_y, 'max_z':max_z,
                                                              'blocks_x':blocks_x, 'blocks_y':blocks_y, 'blocks_z':blocks_z}),
      ('surfaceFeatureExtractDict', f'{case_path}/system/surfaceFeatureExtractDict', {'stl_filename':stl_filename}),
      ('snappyHexMeshDict', f'{case_path}/system/snappyHexMeshDict', {'stl_filename':stl_filename, 'emesh_filename':emesh_filename, 'level_edges':level_edges,
                                                                      'level_surface_min':level_surface_min, 'level_surface_max':level_surface_max,
                                                                      'max_unbalance':max_unbalance}),
      ('meshQualityDict', f'{case_path}/system/meshQualityDict', {}),
      ('sample', f'{case_path}/system/sample', {'points':sample_points}),
      ('allRun', f'{case_path}/allRun', {'case_path':case_path}),
      ('decomposeParDict', f'{case_path}/system/decomposeParDict', {'n_procs':n_procs}),
      ('allRunPar', f'{case_path}/allRunPar', {'case_path':case_path, 'n_procs':n_procs}),
      ('runMesh', f'{case_path}/runMesh', {'case_path':case_path}),
      ('runSim', f'{case_path}/runSim', {'case_path':case_path}),
      ('runMeshPar', f'{case_path}/runMeshPar', {'case_path':case_path, 'n_procs':n_procs}),
      ('runSimPar', f'{case_path}/runSimPar', {'case_path':case_path, 'n_procs':n_procs}),
  ]

  render_env = jinja2.Environment(loader=jinja2.FileSystemLoader('templates'))

  # make simulation files
  for loc, dest, kwargs in render_list:
      template = render_env.get_template(loc)
      content = template.render(**kwargs)
      with open(dest, 'w+') as f:
        f.write(content)

  now = time.perf_counter()
  print('prep time:', now-then)
  then = now
  
  # run mesh
  run_mesh_file = 'runMesh' if n_procs == 1 else 'runMeshPar'
  os.system(f'chmod u+x {case_path}/{run_mesh_file}')
  os.system(f'{case_path}/{run_mesh_file}')

  now = time.perf_counter()
  print('mesh time:', now-then)
  then = now
  
  # run simulation
  run_sim_file = 'runSim' if n_procs == 1 else 'runSimPar'
  os.system(f'chmod u+x {case_path}/{run_sim_file}')
  os.system(f'{case_path}/{run_sim_file}')

  now = time.perf_counter()
  print('simulation time:', now-then)
  then = now

  # sample values into text file
  os.system(f'openfoam2206 postProcess -func sample -case {case_path}')

  now = time.perf_counter()
  print('sample time:', now-then)
  then = now

  sample_dir = sorted(os.listdir('FOAM_case/postProcessing/sample'))

  # read text file to make torch tensor
  n_t = len(sample_dir)
  output = torch.zeros((n_t, n_x, n_y, n_z, 4))
  for k_t, file in enumerate(sample_dir):
    with open(f'FOAM_case/postProcessing/sample/{file}/Uref_p_U.xy') as f:
      for line in f.readlines():
        x, y, z, p, U_x, U_y, U_z = (float(item) for item in line.split())
        k_x = round((x-min_x) / d_x)
        k_y = round((y-min_y) / d_y)
        k_z = round((z-min_z) / d_z)
        output[k_t, k_x, k_y, k_z] = torch.Tensor([p, U_x, U_y, U_z])

  now = time.perf_counter()
  print('tensor make time:', now-then)
  then = now

  now = time.perf_counter()
  print('total:', now-orig_then)

  return output


def default_params():
  params = {
      'airfoil_number': 9430,  # controls airfoil shape 
      'airfoil_n_points': 100,  # n points for airfoil construction
      'airfoil_width': 1,  # dimension perpendicular to flow (meters)
      'airfoil_length': 1,  # dimension parallel to flow (meters)
      'airfoil_attack_angle': 0,  # tilt angle to flow (degrees)
      'domain_inlet_velocity': 50.00,  # flow velocity in +x direction (meters/second)
      'domain_min_x': -2.00,  # domain min in x direction (meters)
      'domain_max_x':  4.00,  # domain max in x direction (meters)
      'domain_min_y': -2.00,  # domain min in y direction (meters)
      'domain_max_y':  2.00,  # domain max in y direction (meters)
      'domain_min_z': -2.00,  # domain min in z direction (meters)
      'domain_max_z':  2.00,  # domain max in z direction (meters)
      'sample_n_x': 151,  # n points to sample in x direction
      'sample_n_y': 101,  # n points to sample in y direction
      'sample_n_z': 101,  # n points to sample in z direction
      'sample_n_t': 1,  # n points to sample through time
      'mesh_resolution_x': 60,  # mesh base resolution in x direction
      'mesh_resolution_y': 40,  # mesh base resolution in y direction
      'mesh_resolution_z': 40,  # mesh base resolution in z direction
      'mesh_level_edges': 2,  # mesh refinement level for edges
      'mesh_level_surface_min': 3,  # min mesh refinement level at airfoil
      'mesh_level_surface_max': 4,  # max mesh refinement level at airfoil
      'sim_delta_t': 1e-5,  # length of one simulation iteration (seconds)
      'sim_write_interval': 100,  # write every n iterations
      'sim_n_procs': 1,  # number of processors
      'sim_max_unbalance': 0.1,  # relative difference in the number of cells per processor
  }
  return params



In [5]:
params = default_params()
params.update({
    'sample_n_t' : 2,
    'mesh_level_surface_min': 2,
    'mesh_level_surface_max': 3,
    'sim_n_procs': 4,
    'sim_max_unbalance': 0.25,
})
q = simulation('FOAM_case', params)

prep time: 3.416733045000001
mesh time: 44.486735571
simulation time: 31.877062287
sample time: 27.522977621000052
tensor make time: 54.47254577199999
total: 161.77717629199998


In [6]:
q.shape

torch.Size([2, 151, 101, 101, 4])

In [ ]:
import numpy
import matplotlib.pyplot as plt
from matplotlib import animation
from matplotlib import rc
rc('animation', html='jshtml')
plt.ioff()


def visual(input, t=None, x=None, y=None, z=None, save=False):
  slices = []
  free_indices = []
  function_indices = []
  for dim_idx, dim_select in enumerate([t, x, y, z]):
    if dim_select is None:
      if dim_idx == 0:
        slices.append(0)
      else:
        slices.append(slice(0, input.size(dim_idx)))
        free_indices.append(dim_idx)
    elif dim_select is ...:
      slices.append(slice(0, input.size(dim_idx)))
      function_indices.append(dim_idx)
    else:
      slices.append(dim_select)
  
  assert len(free_indices) == 2
  assert len(function_indices) < 2
  
  pre_selection = input[slices][..., 0]
  vmin = pre_selection.min()
  vmax = pre_selection.max()
  
  def frame(replacement=None):
  
    if replacement is not None:
      slices[function_indices[0]] = replacement
    selection = input[slices]
    pressure = selection[..., 0]
    velocity = selection[..., 1:]

    background = pressure

    quiver_i = numpy.asarray(range(0, input.size(free_indices[0]), 5))
    quiver_j = numpy.asarray(range(0, input.size(free_indices[1]), 5))
    grid = numpy.meshgrid(quiver_i, quiver_j)
    quiver_vel = velocity[grid]
    quiver_y, quiver_x = grid
    quiver_u = quiver_vel[..., free_indices[1]-1]
    quiver_v = quiver_vel[..., free_indices[0]-1]

    image = plt.imshow(pressure.numpy(), vmin=vmin, vmax=vmax, cmap='jet')
    quiver = plt.quiver(quiver_x, quiver_y, quiver_u, quiver_v, angles='xy')

    return [image, quiver]

  plt.close()
  fig = plt.figure(figsize=(8,8))

  if function_indices:
    my_anim = animation.FuncAnimation(fig, func=frame, frames=range(input.size(function_indices[0])),
                                      interval=100, blit=True)
    if save:
      my_anim.save(f'{save}.mp4')
    return my_anim

  else:
    frame()
    return fig


In [ ]:
visual(q, t=..., z=50, save='t_slices')

In [ ]:
visual(q, t=2, z=..., save='z_slices')

In [8]:

min_x, max_x = (-2,4)
min_y, max_y = (-2,2)
min_z, max_z = (-2,2)
n_x, n_y, n_z = 151, 101, 101

dim_x = max_x - min_x
dim_y = max_y - min_y
dim_z = max_z - min_z
d_x = dim_x / (n_x-1)
d_y = dim_y / (n_y-1)
d_z = dim_z / (n_z-1)

sample_points = list((min_x+k_x*d_x, min_y+k_y*d_y, min_z+k_z*d_z)
                          for k_x in range(n_x) for k_y in range(n_y) for k_z in range(n_z))

In [9]:
import numpy, scipy

with open('FOAM_case/constant/polyMesh/points') as f:
  points_text = f.readlines()
points = [tuple(float(item) for item in line[1:-2].split()) for line in points_text[21:-4]]

with open('FOAM_case/constant/polyMesh/faces') as f:
  faces_text = f.readlines()
faces = [tuple(int(item) for item in line[2:-2].split()) for line in faces_text[21:-4]]

with open('FOAM_case/constant/polyMesh/owner') as f:
  owner_text = f.readlines()
owner = [int(line[:-1]) for line in owner_text[22:-4]]

with open('FOAM_case/constant/polyMesh/neighbour') as f:
  neighbor_text = f.readlines()
neighbor = [int(line[:-1]) for line in neighbor_text[22:-4]]

n_faces = len(faces)
n_cells = max(owner + neighbor) + 1

points_from_face = [list() for _ in range(n_faces)]
for face_id, face in enumerate(faces):
  points_from_face[face_id] += [points[point_id] for point_id in face]

points_from_cell = [list() for _ in range(n_cells)]
for face_id, cell_id in enumerate(owner):
  points_from_cell[cell_id] += points_from_face[face_id]
for face_id, cell_id in enumerate(neighbor):
  points_from_cell[cell_id] += points_from_face[face_id]

centers_of_cells = [None] * n_cells
for cell_id, vertices in enumerate(points_from_cell):
  vertices_numpy = numpy.array(list(set(vertices)))
  centers_of_cells[cell_id] = numpy.mean(vertices_numpy, axis=0)

centers_of_cells_numpy = numpy.stack(centers_of_cells)
centers_of_cells_numpy.shape

(110708, 3)

In [10]:
with open('FOAM_case/constant/polyMesh/boundary') as f:
  boundary_text = f.readlines()
boundary_start_faces = [int(boundary_text[k][:-2].split()[1]) for k in [24, 30, 36, 43]]
boundary_start_faces = dict(zip(['inlet', 'outlet', 'walls', 'airfoil'], boundary_start_faces))

boundary_tri_faces = []
for face in faces[boundary_start_faces['airfoil']: n_faces]:
  for v2, v3 in zip(face[1:], face[2:]):
    boundary_tri_faces.append((points[face[0]], points[v2], points[v3]))

boundary_tri_faces = numpy.asarray(boundary_tri_faces)